In [1]:
import sys
DATA_PATH = "../data/raw/promsvyazbank_reviews.json"

sys.path.append('../pzh')

In [ ]:
import json

data = ""
with open(DATA_PATH) as f:
    data = json.load(f)
data['data']

In [3]:
import pandas as pd
from tqdm import tqdm
df = pd.DataFrame.from_dict(data['data'])

In [4]:
df = df.set_index(df.id)

In [5]:
df.head()

id                                              title  \
id                                                                      
12017118  12017118  Консультация в чате банка по акции «мой суперп...   
12001980  12001980                                   Оформление счета   
11998447  11998447                   Благодарность управляющему офиса   
11994543  11994543                    Предоставили подробности в чате   
11993930  11993930  Понятные условия по продуктам промсвязьбанка, ...   

                                userName  \
id                                         
12017118                user-47287494153   
12001980               user-933720345237   
11998447               user-639720334677   
11994543                        IrSm1965   
11993930  openid.mail.ru/mail/anton_ant_   

                                                       text  grade  \
id                                                                   
12017118  <p>Добрый день. Недавно узнал, что в Промсвязь...    5.0   
12001980  <p>Добрый день! 12 декабря обращался в офис ПС...    5.0   
11998447  <p>    Добрый день!           </p>\r\n<p>    Х...    5.0   
11994543  <p>Я слышала, что за пополнение металлического...    5.0   
11993930  <ul>\r\n<li> Шел после работы вечером 01.11.24...    5.0   

          commentCount  isCountable           dateCreate resolutionIsApproved  \
id                                                                              
12017118             0         True  2024-12-18 14:28:34                 None   
12001980             1         True  2024-12-14 15:49:00                 None   
11998447             1         True  2024-12-13 15:12:18                 None   
11994543             0         True  2024-12-12 16:31:27                 None   
11993930             0         True  2024-12-12 14:15:46                 None   

                                            agentAnswerText  agentId  \
id                                                                     
12017118  Здравствуйте!\r\n\r\nБлагодарим за высокую оце...     5306   
12001980  Здравствуйте!\r\n\r\nСпасибо за Ваш отзыв и до...     5306   
11998447  Здравствуйте!\r\n\r\nБлагодарим Вас за тёплые ...     5306   
11994543  Здравствуйте!\r\n\r\nБлагодарим за обратную св...     5306   
11993930  Здравствуйте!\r\n\r\nБлагодарим за высокую оце...     5306   

                                                    company  hasDocuments  
id                                                                         
12017118  {'id': 5306, 'code': 'promsvyazbank', 'name': ...          True  
12001980  {'id': 5306, 'code': 'promsvyazbank', 'name': ...          True  
11998447  {'id': 5306, 'code': 'promsvyazbank', 'name': ...         False  
11994543  {'id': 5306, 'code': 'promsvyazbank', 'name': ...          True  
11993930  {'id': 5306, 'code': 'promsvyazbank', 'name': ...          True

In [11]:
from enum import Enum
from typing import Optional

from pydantic import BaseModel, Field, ValidationError


def get_enum_values(enum: Enum):
    list(map(lambda x: x.value, enum._member_map_.values()))


class Category(Enum):
    CLAIM = "claim"
    SUGGESTION = "suggestion"
    GRATTITUDE = "grattitude"


class FinancialCatetory(Enum):
    NON_FINANCIAL = 0
    FINANCAIL = 1


class ReasonCategory(Enum):
    EMPLOYEE_ERROR = "employee_error"
    TERMS = "terms"
    TECHINCAL = "techincal"
    SERVICE_SPEED = "service_speed"


class Classification(BaseModel):
    """
    Классификация отзывов о банке.
    category
    """
    review_category: int = Field(..., description="0 - Претензия, 1 -  Предложение, 2 - Благодарность")
    financial: int = Field(..., description="1 если финансовое, 0 если нет")
    reason_category: int = Field(..., description="0 - Ошибка сотрудника; 1 - Несогласие с тарифами; 2 - Технический сбой; 3 - Скорость обслуживания;")

In [16]:
import os

from langchain_core.prompts import ChatPromptTemplate
from langchain_core.messages import HumanMessage, SystemMessage
from langchain_gigachat.chat_models import GigaChat

import config


llm = GigaChat(
    credentials=os.environ.get('GIGA_ACCESS_KEY'),
    scope="GIGACHAT_API_PERS",
    model="GigaChat",
    # Отключает проверку наличия сертификатов НУЦ Минцифры
    verify_ssl_certs=False,
    streaming=False,
).with_structured_output(Classification)



2024-12-20 22:52:21.752 | INFO     | config:<module>:11 - PROJ_ROOT path is: /home/itcenter/AvaiaHack2024/pzh


In [17]:
tagging_prompt = ChatPromptTemplate.from_messages(
    [
        SystemMessage(content="""
Ты - помощник для классификации отзывов о банке. 
В ответе предоставь строго JSON с полями 'review_category', 'financial' и 'reason_category', без дополнительного текста. 

Правила классификации 'review_category':
- 0: Претензия (например, "Недоволен", "Плохо", "Ужасно", "Почему так долго?", "Разочарован", есть выраженное недовольство)
- 1: Предложение (например, "Я думаю, вы могли бы улучшить...","Предлагаю сделать...")
- 2: Благодарность (например, "Спасибо", "Благодарю", "Отлично", "Мне всё понравилось")

Если клиент благодарит или доволен, без претензий – выбирай 2 (благодарность).

financial:
- 1 если претензия или предложение затрагивает финансовые условия (тарифы, проценты, деньги)
- 0 иначе

reason_category:
- 0: Ошибка сотрудника (упоминание конкретных сотрудников или офисов, намёк на человеческий фактор)
- 1: Тарифы/условия (слова «Тариф/Правила/Договор»)
- 2: Тех.сбой («Сбой/Авария/Проблема/Завис»)
- 3: Скорость обслуживания («Медленно/Долго/Быстро/Оперативно»)

Убедись, что при благодарности нет лишних жалоб. 
Пример:
"Спасибо за быстрое обслуживание" -> review_category: 2, financial: 0, reason_category: 3

"""),
        HumanMessage(content="""
Выдели необходимую информацмию из отзыва о банке.
Верни только JSON, соответствующий модели 'Classification'. 
Название: {title}
Оценка: {grade}
Текст:
{text}
""")
]

)


In [9]:
# from langchain_ollama import ChatOllama
# llm = ChatOllama(model="herenickname/t-tech_T-lite-it-1.0:q4_k_m").with_structured_output(Classification)

In [21]:
from langchain_openai import ChatOpenAI
llm = ChatOpenAI(model="t-tech/T-lite-it-1.0", api_key="EMPTY", base_url="http://localhost:8000/v1").with_structured_output(Classification)

In [19]:
# from langchain_community.llms import VLLM
# llm = VLLM(
#     model="t-tech/T-lite-it-1.0",
#     trust_remote_code=True,  # mandatory for hf models
#     max_new_tokens=128,
#     top_k=10,
#     top_p=0.95,
#     temperature=0.8,
#     quantization="bitsandbytes", load_format="bitsandbytes",
#     # gpu_memory_utilization=
# ).with_structured_output(Classification)

INFO 12-20 22:25:38 config.py:478] This model supports multiple tasks: {'embed', 'reward', 'score', 'classify', 'generate'}. Defaulting to 'generate'.
INFO 12-20 22:25:38 llm_engine.py:249] Initializing an LLM engine (v0.6.5) with config: model='t-tech/T-lite-it-1.0', speculative_config=None, tokenizer='t-tech/T-lite-it-1.0', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, tokenizer_revision=None, trust_remote_code=True, dtype=torch.bfloat16, max_seq_len=32768, download_dir=None, load_format=auto, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=None, enforce_eager=False, kv_cache_dtype=auto, quantization_param_path=None, device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='xgrammar'), observability_config=ObservabilityConfig(otlp_traces_endpoint=None, collect_model_forward_time=False, collect_model_execute_time=False), seed=0, served_model_name=t-tech/T-lite-it-1.0, num_sc

Loading safetensors checkpoint shards:   0% Completed | 0/4 [00:00<?, ?it/s]


INFO 12-20 22:26:10 model_runner.py:1097] Loading model weights took 14.2348 GB
INFO 12-20 22:35:28 worker.py:241] Memory profiling takes 557.60 seconds
INFO 12-20 22:35:28 worker.py:241] the current vLLM instance can use total_gpu_memory (24.00GiB) x gpu_memory_utilization (0.90) = 21.60GiB
INFO 12-20 22:35:28 worker.py:241] model weights take 14.23GiB; non_torch_memory takes -10.33GiB; PyTorch activation peak memory takes 4.34GiB; the rest of the memory reserved for KV Cache is 13.35GiB.
INFO 12-20 22:35:28 gpu_executor.py:76] # GPU blocks: 15628, # CPU blocks: 4681
INFO 12-20 22:35:28 gpu_executor.py:80] Maximum concurrency for 32768 tokens per request: 7.63x
INFO 12-20 22:35:30 model_runner.py:1413] Capturing cudagraphs for decoding. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI.
INFO 12-20 22:35:30 model_runner.py:1417] If out-of-memory error occurs during cudagraph 

NotImplementedError: 

In [19]:
print(df.iloc[0].text)

<p>Добрый день. Недавно узнал, что в Промсвязьбанке проходит акция "мой суперприз". И решил обратится 18 декабря 2024 года в 13-50 в чат банка за подробными разъяснениями по данной акции. 

Оператор Карина моментально подключилась к диалогу, вежливо поздоровалась со мной и предоставила мне все необходимые разъяснения по данному вопросу. Также она включила меня в данную акцию непосредственно в чате. А также дала всю необходимую информацию, какой именно я должен открыть вклад и на какой срок, чтобы соблюсти все условия данной акции.</p>
<p>На оставшиеся мои вопросы ответила оператор Вероника и помогла мне окончательно разобраться в данном вопросе. Спасибо большое за оперативную и грамотную консультацию. Сам бы я не разобрался.</p>
<p></p>


In [22]:
row = df.iloc[0]
prompt = tagging_prompt.invoke({"title": row.title, "text": row.text, "grade": row.grade})
llm_resp = llm.invoke(prompt)

llm_resp 

Classification(review_category=2, financial=0, reason_category=3)

In [26]:
chain = tagging_prompt | llm

In [15]:
df.iloc[0]

id                                                               12017118
title                   Консультация в чате банка по акции «мой суперп...
userName                                                 user-47287494153
text                    <p>Добрый день. Недавно узнал, что в Промсвязь...
grade                                                                 5.0
commentCount                                                            0
isCountable                                                          True
dateCreate                                            2024-12-18 14:28:34
resolutionIsApproved                                                 None
agentAnswerText         Здравствуйте!\r\n\r\nБлагодарим за высокую оце...
agentId                                                              5306
company                 {'id': 5306, 'code': 'promsvyazbank', 'name': ...
hasDocuments                                                         True
Name: 12017118, dtype: object

In [16]:
next(df.iterrows())

(12017118,
 id                                                               12017118
 title                   Консультация в чате банка по акции «мой суперп...
 userName                                                 user-47287494153
 text                    <p>Добрый день. Недавно узнал, что в Промсвязь...
 grade                                                                 5.0
 commentCount                                                            0
 isCountable                                                          True
 dateCreate                                            2024-12-18 14:28:34
 resolutionIsApproved                                                 None
 agentAnswerText         Здравствуйте!\r\n\r\nБлагодарим за высокую оце...
 agentId                                                              5306
 company                 {'id': 5306, 'code': 'promsvyazbank', 'name': ...
 hasDocuments                                                         True
 Name: 1201711

In [17]:
df.loc[12017118]

id                                                               12017118
title                   Консультация в чате банка по акции «мой суперп...
userName                                                 user-47287494153
text                    <p>Добрый день. Недавно узнал, что в Промсвязь...
grade                                                                 5.0
commentCount                                                            0
isCountable                                                          True
dateCreate                                            2024-12-18 14:28:34
resolutionIsApproved                                                 None
agentAnswerText         Здравствуйте!\r\n\r\nБлагодарим за высокую оце...
agentId                                                              5306
company                 {'id': 5306, 'code': 'promsvyazbank', 'name': ...
hasDocuments                                                         True
Name: 12017118, dtype: object

In [ ]:
async def classify_text(text, llm):
    

In [27]:
from tqdm import tqdm


classif_results = {"review_category": [], "financial": [], "reason_category": []}
for frow in tqdm(df.iterrows(), total=len(df)):
    row = frow[1]
    max_retries = 3
    for attempt in range(max_retries):
        try:
            llm_resp = await chain.ainvoke({"title": row.title, "text": row.text, "grade": row.grade})
            if llm_resp:
                classif_results['review_category'].append(llm_resp.review_category)
                classif_results['financial'].append(llm_resp.financial)
                classif_results['reason_category'].append(llm_resp.reason_category)
            # If we reach here, parsing succeeded
            break
        except ValidationError as e:
            # If parsing failed, we can adjust the prompt or just retry
            # Optionally, add some logic to refine the prompt
            if attempt < max_retries - 1:
                print("Parsing failed, retrying...")
            else:
                print("Parsing failed after multiple attempts.")
                continue

  0%|▏                                                                              | 18/7882 [00:13<1:39:55,  1.31it/s]


CancelledError: 

In [ ]:
async def get_response(idx, chain, row)

In [ ]:
from tqdm import tqdm
from tqdm.asyncio import tqdm as tqdm_async
import asyncio

async def classify_row(idx, row, llm, max_retries=3):
    for attempt in range(max_retries):
        try:
            # Simulate an async LLM call (replace with your LLM code)
            llm_resp = await llm.ainvoke({"title": row.title, "text": row.text, "grade": row.grade})
            return idx, llm_resp.review_category, llm_resp.financial, llm_resp.reason_category
        except Exception:
            if attempt < max_retries - 1:
                pass
            else:
                return None

async def main(df, llm):
    tasks = [classify_row(idx, row, llm) for idx, row in df.iterrows()]

    results = await tqdm_async.gather(*tasks)

    
    classif_results = {
        "id": [],
        "review_category": [],
        "financial": [],
        "reason_category": [],
    }
    for r in results:
        classif_results["id"].append(r[0])
        classif_results["review_category"].append(r[1])
        classif_results["financial"].append(r[2])
        classif_results["reason_category"].append(r[3])

    return classif_results

await main(df, chain)

In [ ]:
import asyncio
from concurrent.futures import ThreadPoolExecutor
from tqdm import tqdm

async def classify_row_sync(row, llm, prompt, max_retries=3):
    for attempt in range(max_retries):
        try:
            # Blocking call
            llm_resp = await llm.ainvoke(prompt)
            return llm_resp.review_category, llm_resp.financial, llm_resp.reason_category
        except Exception:
            if attempt < max_retries - 1:
                print(f"Retrying row {row.name}...")
            else:
                return
async def main(df, llm, prompt):
    loop = asyncio.get_running_loop()


    
    # Create a ThreadPoolExecutor to run tasks in parallel threads
    with ThreadPoolExecutor() as executor:
        # Submit all rows to the thread pool
        tasks = [
            loop.run_in_executor(executor, classify_row_sync, row, llm, prompt)
            for _, row in df.iterrows()
        ]


       tasks = [process_row(index, row, llm) for index, row in df.iterrows()]
        pbar = tqdm(total=len(tasks), desc="Classifying rows")
        
        # Use asyncio.as_completed to process tasks as they finish
        for coro in asyncio.as_completed(tasks):
            result = await coro
            results.append(result)
            pbar.update(1)  # Update progress after each task completes

        pbar.close()

    # Collect results
    classif_results = {
        "review_category": [r[0] for r in results],
        "financial": [r[1] for r in results],
        "reason_category": [r[2] for r in results],
    }
    return classif_results

# Example usage:
# results = asyncio.run(main(df, llm, prompt))


# Run the async routine
final_results = await main(df, llm, prompt)
print(final_results)

Retrying row 11982639...
Retrying row 11979531...
Retrying row 11979307...
Retrying row 11979914...
Retrying row 11982957...
Retrying row 11979762...
Retrying row 11979100...
Retrying row 11980473...
Retrying row 11979188...
Retrying row 11978963...
Retrying row 11982639...
Retrying row 11979307...
Retrying row 11979914...
Retrying row 11979762...
Retrying row 11979531...
Retrying row 11979100...
Retrying row 11980473...
Retrying row 11982957...
Retrying row 11979188...
Retrying row 11978963...
Retrying row 11978918...


Classifying rows:   0%|          | 0/7882 [00:00<?, ?it/s]

Retrying row 11978275...
Retrying row 11978547...
Retrying row 11975869...
Retrying row 11975832...
Retrying row 11978918...
Retrying row 11977009...
Retrying row 11974921...
Retrying row 11975434...
Retrying row 11978275...
Retrying row 11975450...
Retrying row 11978547...
Retrying row 11974558...
Retrying row 11975869...
Retrying row 11975832...
Retrying row 11977009...
Retrying row 11974921...
Retrying row 11975434...
Retrying row 11974558...
Retrying row 11975450...
Retrying row 11973906...
Retrying row 11973073...
Retrying row 11973011...
Retrying row 11972983...
Retrying row 11971990...
Retrying row 11973906...
Retrying row 11971829...
Retrying row 11970931...
Retrying row 11971719...
Retrying row 11973073...
Retrying row 11973011...
Retrying row 11970301...
Retrying row 11972983...
Retrying row 11970193...
Retrying row 11971990...
Retrying row 11971829...
Retrying row 11970931...
Retrying row 11971719...
Retrying row 11970301...
Retrying row 11970193...
Retrying row 11968640...


Failed to multipart ingest runs: langsmith.utils.LangSmithRateLimitError: Rate limit exceeded for https://api.smith.langchain.com/runs/multipart. HTTPError('429 Client Error: Too Many Requests for url: https://api.smith.langchain.com/runs/multipart', '{"detail":"Monthly unique traces usage limit exceeded"}')trace=eb29d8b4-28f9-4593-bca6-2b8a0d56a83e,id=eb29d8b4-28f9-4593-bca6-2b8a0d56a83e; trace=eb29d8b4-28f9-4593-bca6-2b8a0d56a83e,id=75d2538d-71bc-42e9-8aef-3537cf33e4ca; trace=185ea890-1d7c-438e-9cf2-7c35660eecaa,id=185ea890-1d7c-438e-9cf2-7c35660eecaa; trace=185ea890-1d7c-438e-9cf2-7c35660eecaa,id=9da3038f-6398-4dfa-b2a3-4b0edb1de291; trace=189142f7-c8eb-43ff-9781-39657ca3e015,id=189142f7-c8eb-43ff-9781-39657ca3e015; trace=189142f7-c8eb-43ff-9781-39657ca3e015,id=cdd605a4-a86b-408f-a094-1c57663fca11; trace=ea220041-33fa-4ca4-91c7-6c708e96c1d1,id=ea220041-33fa-4ca4-91c7-6c708e96c1d1; trace=ea220041-33fa-4ca4-91c7-6c708e96c1d1,id=139bd525-4040-46de-8add-3dfa7a44db84; trace=171bfc63-f535

RuntimeError: Failed to classify row 11979307 after 3 attempts

In [62]:
clasif_results

[]